In [43]:
# %pip install numpy
# %pip install pandas
# %pip install matplotlib
# %pip install seaborn
# %pip install scipy
# %pip install sympy

In [44]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
import scipy
import sympy as sp
import math
from sympy import symbols, cos ,log, diff


In [45]:
def fixed_point_iteration(g, x0, tol=1e-3, max_iter=100):
    """
    Método do Ponto Fixo para encontrar a raiz de f(x) = 0,
    usando uma função g(x) tal que x = g(x).

    :param g: Função g(x) usada para a iteração.
    :param x0: Valor inicial (chute).
    :param tol: Tolerância para o erro.
    :param max_iter: Número máximo de iterações.
    :return: A raiz aproximada, número de iterações e lista de aproximações.
    """
    iter_count = 0
    x = x0
    values = [x0]

    while iter_count < max_iter:
        x_next = g(x)
        values.append(x_next)

        if abs(x_next - x) < tol:
            return x_next, iter_count + 1, values, [abs(values[i+1] - values[i]) for i in range(len(values)-1)]

        x = x_next
        iter_count += 1

    raise Exception("O método não convergiu dentro do número máximo de iterações.")


In [46]:
def plot_function(f, x_range):
    """
    Plota a função f(x) em um intervalo x_range.
    """
    x_vals = np.linspace(x_range[0], x_range[1], 400)
    y_vals = f(x_vals)

    # Cria o gráfico da função
    fig_fx = go.Figure()
    fig_fx.add_trace(go.Scatter(x=x_vals, y=y_vals,
                                mode='lines',
                                name='f(x) = x² + x - 6',
                                line=dict(color='darkblue', width=2)))

    fig_fx.show()

In [47]:
def fpi_print_history(g, x0, tol=1e-3, max_iter=100):
    try:
        root, iters, history, errors = fixed_point_iteration(g, x0, tol=tol, max_iter=max_iter)
        print(f"Raiz aproximada: {root}")
        print(f"Número de iterações: {iters}")
        print("Histórico de aproximações:")
        for i, val in enumerate(history):
            print(f"  Iteração {i}: {val}")
        print("Histórico de erros:")
        for i, err in enumerate(errors):
            print(f"  Iteração {i}: {err}")
        return root, iters, history, errors
    except Exception as e:
        print(f"Erro: {e}")
        print("OS error info:", getattr(e, 'errno', None), getattr(e, 'strerror', None))
        return None, None, None, None

In [48]:
def fpi_plot_history(history):
    try:
        fig = px.line(
            x=list(range(len(history))),
            y=history,
            markers=True,
            labels={'x': 'Iteração', 'y': 'Aproximação'},
            title='Histórico de Aproximações - Método do Ponto Fixo',
        )
        fig.update_traces(
            marker=dict(size=10, color='red', line=dict(width=2, color='DarkSlateGrey')),
            line=dict(width=2, color='blue')
        )
        fig.show()
    except Exception as e:
        print("Erro ao plotar o gráfico:", e)
        return None

In [76]:
def fpi_plot_graph(f, history, root, g_label="g(x)", errors=None):
    """
    Plota f(x), as aproximações do método do ponto fixo, destaca a raiz aproximada e plota o erro.
    """
    if history is None or root is None:
        print("Histórico ou raiz não definidos.")
        return

    x_vals = np.linspace(min(history) - 1, max(history) + 1, 4000)
    y_vals = f(x_vals)

    fig_fx = go.Figure()
    fig_fx.add_trace(go.Scatter(x=x_vals, y=y_vals,
                                mode='lines',   
                                name='f(x)',
                                line=dict(color='darkblue', width=2)))

    fig_fx.add_trace(go.Scatter(x=history, y=[f(x) for x in history], 
                                mode='markers+lines', 
                                name=g_label,
                                marker=dict(size=7, color='red', line=dict(width=2, color='DarkSlateGrey'))))

    fig_fx.add_trace(go.Scatter(x=[root], y=[f(root)], mode='markers', name='Raiz Aproximada',
                                marker=dict(size=10, color='orange', symbol='cross', line=dict(width=2, color='Black'))))

    fig_fx.update_layout(title='f(x) e Aproximações pelo Método do Ponto Fixo',
                        xaxis_title='x',
                        yaxis_title='f(x)',
                        showlegend=True)
                        
    fig_fx.show()

    # Plotando o erro, se fornecido
    if errors is not None:
        fig_err = go.Figure()
        fig_err.add_trace(go.Scatter(
            x=list(range(1, len(errors)+1)),
            y=errors,
            mode='markers+lines',
            name='Erro',
            marker=dict(size=7, color='green', line=dict(width=2, color='DarkSlateGrey'))
        ))
        fig_err.update_layout(title='Erro em cada Iteração',
                             xaxis_title='Iteração',
                             yaxis_title='Erro')
        fig_err.show()


In [77]:
def fpi_plot_analysis(x_vals, g_vals,f = lambda x: x**2):
    """
    Generates a plot for graphical analysis of fixed points in the fixed-point iteration method.

    Parameters:
    - x_vals (array-like): Values of x in the domain of the function.
    - g_vals (array-like): Values of the function g(x) corresponding to x_vals.

    The plot includes:
    - The function f(x) = x^2 + x - 6.
    - The function g(x).
    - The identity line y = x (fixed points line).
    - The numerical derivative g'(x).
    - Reference lines at y = 1 and y = -1 for convergence analysis.

    Returns:
    - Interactively displays the plot.
    """

    

    if len(x_vals) != len(g_vals):
        raise ValueError("x_vals e g_vals devem ter o mesmo comprimento.")

    g_deriv = np.gradient(g_vals, x_vals)

    fig = go.Figure()

    # Plot f(x)
    y_vals = f(x_vals)
    fig.add_trace(go.Scatter(
        x=x_vals, y=y_vals,
        mode='lines',
        name='f(x)',
        line=dict(color='purple', width=2)
    ))

    # Plot g(x)
    fig.add_trace(go.Scatter(
        x=x_vals, y=g_vals,
        mode='lines',
        name='g(x)',
        line=dict(color='blue')
    ))

    # Plot y = x
    fig.add_trace(go.Scatter(
        x=x_vals, y=x_vals,
        mode='lines',
        name='y = x',
        line=dict(dash='dash', color='black')
    ))

    # Plot g'(x)
    fig.add_trace(go.Scatter(
        x=x_vals, y=g_deriv,
        mode='lines',
        name="g'(x)",
        line=dict(dash='dot', color='green')
    ))

    # Plot y = -1 and y = 1
    for y_ref in [-1, 1]:
        fig.add_trace(go.Scatter(
            x=[x_vals[0], x_vals[-1]],
            y=[y_ref, y_ref],
            mode='lines',
            name=f'y = {y_ref}',
            line=dict(color='gray', dash='dot')
        ))
    # Plot y = 0
    for y_ref in [0]:
        fig.add_trace(go.Scatter(
            x=[x_vals[0], x_vals[-1]],
            y=[y_ref, y_ref],
            mode='lines',
            name=f'y = {y_ref}',
            line=dict(color='gray')
        ))

    # # Layout
    y_min = min(-1, np.min(g_vals), np.min(g_deriv))
    y_max = max(1, np.max(g_vals), np.max(g_deriv))

    fig.update_layout(
        title='Graphical Analysis of Fixed Points',
        xaxis_title='x',
        yaxis_title='y',
        legend_title='Functions',
        showlegend=True,
        xaxis=dict(
            title='x',
            tickmode='linear'
        ),
        yaxis=dict(
            title='y',
            range=[y_min, y_max],
            tickmode='linear',
            dtick=0.5
        )
    )
    return fig


In [51]:
def symbolic_derivative(g):
    x = symbols('x')
    g_sym = g(x)
    g_prime = diff(g_sym, x)
    print("Symbolic derivative:", g_prime)
    return g_prime

## teste

## f(x) = x^2 + x - 6
```python

In [71]:
f = lambda x: x**2 + x - 6

```markdown
g(x) = sqrt(6-x)

In [72]:
g = lambda x: math.sqrt(6 - x)  # g(x) = sqrt(6 - x)

In [73]:
x0 = -0.2

_r, _i, history, errors = fpi_print_history(g, x0)

Raiz aproximada: 2.000122761378024
Número de iterações: 7
Histórico de aproximações:
  Iteração 0: -0.2
  Iteração 1: 2.4899799195977463
  Iteração 2: 1.8735047585747557
  Iteração 3: 2.0313776708001012
  Iteração 4: 1.9921401379420822
  Iteração 5: 2.001964001189312
  Iteração 6: 1.999508939417548
  Iteração 7: 2.000122761378024
Histórico de erros:
  Iteração 0: 2.6899799195977465
  Iteração 1: 0.6164751610229906
  Iteração 2: 0.1578729122253455
  Iteração 3: 0.03923753285801901
  Iteração 4: 0.009823863247229614
  Iteração 5: 0.0024550617717638
  Iteração 6: 0.0006138219604758799


In [74]:
fpi_plot_history(history)

In [79]:
fpi_plot_graph(f, history, _r, g_label="g(x) = sqrt(6 - x)", errors=errors)

In [80]:
symbolic_derivative(g = lambda x: sp.sqrt(6 - x))

Symbolic derivative: -1/(2*sqrt(6 - x))


-1/(2*sqrt(6 - x))

In [81]:
g = lambda x: np.sqrt(6 - x)  # g(x) = sqrt(6 - x)
x_vals = np.linspace(min(history) - 20, max(history) + 20, 4000)
g_vals = g(x_vals)

fpi_plot_analysis(
    x_vals=x_vals,
    g_vals=g_vals,
    f=f
)

/var/folders/bp/qdzsf2qn79s699cch8zgb0rr0000gp/T/ipykernel_21907/3904308631.py:1: RuntimeWarning:

invalid value encountered in sqrt



## math domain error
```python

### ocorre quando alguma iteração de uma função matemática não é válida, nesse caso a raiz quadrada de um número negativo
```python

### exemplo: g(7)
sqrt(6-7) = sqrt(-1) = math domain error
``` 

In [82]:
g = lambda x: math.sqrt(6-x)
x0 = 7

try:
    root, iters, history = fixed_point_iteration(g, x0)
    print(f"Raiz aproximada: {root}")
    print(f"Número de iterações: {iters}")
    print("Histórico de aproximações:")
    for i, val in enumerate(history):
        print(f"  Iteração {i}: {val}")
except Exception as e:
    print(e)

math domain error


### exemplo: g(-31)
a função g(-31) gera um erro, mas não na primeira iteração, e nas próximas.
```python
``` 

In [83]:
g = lambda x: math.sqrt(6-x)
x0 = -31

try:
    root, iters, history = fixed_point_iteration(g, x0)
    print(f"Raiz aproximada: {root}")
    print(f"Número de iterações: {iters}")
    print("Histórico de aproximações:")
    for i, val in enumerate(history):
        print(f"  Iteração {i}: {val}")
except Exception as e:
    print(e,e.__doc__)

math domain error Inappropriate argument value (of correct type).


In [84]:
g = lambda x: math.sqrt(6-x)
w1 = g(-31)
w1

6.082762530298219

In [85]:
try:
    g(w1)
except Exception as e:
    print("Erro ao calcular g(w1):", e,e.__doc__)

Erro ao calcular g(w1): math domain error Inappropriate argument value (of correct type).


### essa função de iteração só pode ser implementada para valores contidos no intervalo [-30, 6]
```python
``` 

# exemplo 11

```python
``` 

In [86]:
g = lambda x: math.sqrt(6-x)
x0 = -31

try:
    root, iters, history = fixed_point_iteration(g, x0)
    print(f"Raiz aproximada: {root}")
    print(f"Número de iterações: {iters}")
    print("Histórico de aproximações:")
    for i, val in enumerate(history):
        print(f"  Iteração {i}: {val}")
except Exception as e:
    print(e,e.__doc__)

math domain error Inappropriate argument value (of correct type).


# cos(ln(x))-x/2
```python
``` 

In [87]:
f = lambda x: np.cos(np.log(x)) - x/2

```markdown
g(x) = sqrt(6-x)

In [88]:
g = lambda x: np.cos(np.log(x)) * 2

In [90]:
x0 = 4

_r, _i, history, errors = fpi_print_history(g, x0)

Raiz aproximada: 1.7152790288882682
Número de iterações: 16
Histórico de aproximações:
  Iteração 0: 4
  Iteração 1: 0.36691394948660344
  Iteração 2: 1.0761782343583914
  Iteração 3: 1.9946124977432524
  Iteração 4: 1.5419192518064584
  Iteração 5: 1.8153986768300758
  Iteração 6: 1.6548325472874716
  Iteração 7: 1.7516055388684537
  Iteração 8: 1.6939439302628625
  Iteração 9: 1.7285797213903225
  Iteração 10: 1.7078652316726088
  Iteração 11: 1.7202882130466568
  Iteração 12: 1.7128497477869598
  Iteração 13: 1.7173080132695542
  Iteração 14: 1.7146374849264123
  Iteração 15: 1.7162377068981072
  Iteração 16: 1.7152790288882682
Histórico de erros:
  Iteração 0: 3.6330860505133966
  Iteração 1: 0.709264284871788
  Iteração 2: 0.918434263384861
  Iteração 3: 0.45269324593679405
  Iteração 4: 0.27347942502361744
  Iteração 5: 0.16056612954260419
  Iteração 6: 0.09677299158098207
  Iteração 7: 0.05766160860559122
  Iteração 8: 0.03463579112745996
  Iteração 9: 0.020714489717713613
  Ite

In [91]:
fpi_plot_history(history)

In [94]:
fpi_plot_graph(f, history, _r, g_label="g(x) = np.cos(np.log(x)) * 2", errors=errors)

/var/folders/bp/qdzsf2qn79s699cch8zgb0rr0000gp/T/ipykernel_21907/2409415758.py:1: RuntimeWarning:

invalid value encountered in log



In [95]:
symbolic_derivative(g = lambda x: 2 * sp.cos(sp.log(x)))

Symbolic derivative: -2*sin(log(x))/x


-2*sin(log(x))/x

In [96]:

x_vals = np.linspace(min(history) - 2, max(history) + 2, 40000)
g_vals = g(x_vals)

fpi_plot_analysis(
    x_vals=x_vals,
    g_vals=g_vals,
    f=f
)

/var/folders/bp/qdzsf2qn79s699cch8zgb0rr0000gp/T/ipykernel_21907/1277808751.py:1: RuntimeWarning:

invalid value encountered in log



Exemplo 11 

In [ ]:
f = lambda x: np.float64(x**3 - 9*x + 3)

```markdown
g(x) = sqrt(6-x)

In [ ]:
g = lambda x: np.float64(x**3 + 3) / 9

In [ ]:
x0 = 0.5

_r, _i, history = fpi_print_history(g, x0, tol=1e-3)

Raiz aproximada: 0.33762324738031935
Número de iterações: 3
Histórico de aproximações:
  Iteração 0: 0.5
  Iteração 1: 0.3472222222222222
  Iteração 2: 0.33798469412056087
  Iteração 3: 0.33762324738031935


In [ ]:
fpi_plot_history(history)

In [ ]:
fpi_plot_graph(f, history, _r, g_label="g(x)")

In [ ]:
symbolic_derivative(g = lambda x: 2 * (x**3 + 3) / 9)

Symbolic derivative: 2*x**2/3


2*x**2/3

In [ ]:

x_vals = np.linspace(min(history) - 2, max(history) + 2, 40000)
g_vals = g(x_vals)

fpi_plot_analysis(
    x_vals=x_vals,
    g_vals=g_vals,
    f=f
)